In [8]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [9]:
# Convolutional neural network (two convolutional layers)
class BiRNN(nn.Module):
    def __init__(self, num_classes=4):
        super(BiRNN, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64,affine=False)
        self.ac1 = nn.Softplus()
        self.rnn = nn.RNN(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        
    def forward(self, x):      
        x, _= self.rnn(x)
        #print(x.shape)
        #print(x.shape)
        x = x[:,-1,:]
        #print(x.shape)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.ac1(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [10]:
rnn = BiRNN(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 4])


In [11]:
writer = SummaryWriter()

In [12]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [13]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [14]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [15]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [16]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [17]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [18]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [20]:
model = BiRNN(num_classes).to(device)

In [21]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [22]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 32.8125%, Training Loss: 1.4744%
Epoch [1/300], Step [2/225], Training Accuracy: 32.8125%, Training Loss: 1.4456%
Epoch [1/300], Step [3/225], Training Accuracy: 31.7708%, Training Loss: 1.4697%
Epoch [1/300], Step [4/225], Training Accuracy: 30.4688%, Training Loss: 1.4925%
Epoch [1/300], Step [5/225], Training Accuracy: 30.6250%, Training Loss: 1.4899%
Epoch [1/300], Step [6/225], Training Accuracy: 29.9479%, Training Loss: 1.5006%
Epoch [1/300], Step [7/225], Training Accuracy: 30.1339%, Training Loss: 1.4916%
Epoch [1/300], Step [8/225], Training Accuracy: 28.9062%, Training Loss: 1.4926%
Epoch [1/300], Step [9/225], Training Accuracy: 28.8194%, Training Loss: 1.4782%
Epoch [1/300], Step [10/225], Training Accuracy: 28.2812%, Training Loss: 1.4760%
Epoch [1/300], Step [11/225], Training Accuracy: 28.1250%, Training Loss: 1.4770%
Epoch [1/300], Step [12/225], Training Accuracy: 27.4740%, Training Loss: 1.4771%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [104/225], Training Accuracy: 27.8395%, Training Loss: 1.4198%
Epoch [1/300], Step [105/225], Training Accuracy: 27.7827%, Training Loss: 1.4201%
Epoch [1/300], Step [106/225], Training Accuracy: 27.8302%, Training Loss: 1.4199%
Epoch [1/300], Step [107/225], Training Accuracy: 27.8768%, Training Loss: 1.4196%
Epoch [1/300], Step [108/225], Training Accuracy: 27.8501%, Training Loss: 1.4195%
Epoch [1/300], Step [109/225], Training Accuracy: 27.8240%, Training Loss: 1.4190%
Epoch [1/300], Step [110/225], Training Accuracy: 27.8835%, Training Loss: 1.4189%
Epoch [1/300], Step [111/225], Training Accuracy: 27.8716%, Training Loss: 1.4189%
Epoch [1/300], Step [112/225], Training Accuracy: 27.9018%, Training Loss: 1.4187%
Epoch [1/300], Step [113/225], Training Accuracy: 27.9729%, Training Loss: 1.4188%
Epoch [1/300], Step [114/225], Training Accuracy: 27.9605%, Training Loss: 1.4187%
Epoch [1/300], Step [115/225], Training Accuracy: 27.9755%, Training Loss: 1.4188%
Epoc

Epoch [1/300], Step [215/225], Training Accuracy: 28.6483%, Training Loss: 1.4049%
Epoch [1/300], Step [216/225], Training Accuracy: 28.6820%, Training Loss: 1.4046%
Epoch [1/300], Step [217/225], Training Accuracy: 28.7010%, Training Loss: 1.4043%
Epoch [1/300], Step [218/225], Training Accuracy: 28.6841%, Training Loss: 1.4045%
Epoch [1/300], Step [219/225], Training Accuracy: 28.7743%, Training Loss: 1.4037%
Epoch [1/300], Step [220/225], Training Accuracy: 28.8139%, Training Loss: 1.4033%
Epoch [1/300], Step [221/225], Training Accuracy: 28.7825%, Training Loss: 1.4033%
Epoch [1/300], Step [222/225], Training Accuracy: 28.8218%, Training Loss: 1.4031%
Epoch [1/300], Step [223/225], Training Accuracy: 28.7906%, Training Loss: 1.4032%
Epoch [1/300], Step [224/225], Training Accuracy: 28.7667%, Training Loss: 1.4033%
Epoch [1/300], Step [225/225], Training Accuracy: 28.7521%, Training Loss: 1.4035%
Epoch [2/300], Step [1/225], Training Accuracy: 32.8125%, Training Loss: 1.3780%
Epoch 

Epoch [2/300], Step [111/225], Training Accuracy: 30.4476%, Training Loss: 1.3669%
Epoch [2/300], Step [112/225], Training Accuracy: 30.4827%, Training Loss: 1.3665%
Epoch [2/300], Step [113/225], Training Accuracy: 30.5448%, Training Loss: 1.3666%
Epoch [2/300], Step [114/225], Training Accuracy: 30.5784%, Training Loss: 1.3661%
Epoch [2/300], Step [115/225], Training Accuracy: 30.5435%, Training Loss: 1.3664%
Epoch [2/300], Step [116/225], Training Accuracy: 30.5630%, Training Loss: 1.3664%
Epoch [2/300], Step [117/225], Training Accuracy: 30.5155%, Training Loss: 1.3667%
Epoch [2/300], Step [118/225], Training Accuracy: 30.4423%, Training Loss: 1.3669%
Epoch [2/300], Step [119/225], Training Accuracy: 30.4491%, Training Loss: 1.3670%
Epoch [2/300], Step [120/225], Training Accuracy: 30.5339%, Training Loss: 1.3667%
Epoch [2/300], Step [121/225], Training Accuracy: 30.5398%, Training Loss: 1.3668%
Epoch [2/300], Step [122/225], Training Accuracy: 30.5200%, Training Loss: 1.3669%
Epoc

Epoch [3/300], Step [3/225], Training Accuracy: 33.3333%, Training Loss: 1.3838%
Epoch [3/300], Step [4/225], Training Accuracy: 33.2031%, Training Loss: 1.3825%
Epoch [3/300], Step [5/225], Training Accuracy: 33.4375%, Training Loss: 1.3921%
Epoch [3/300], Step [6/225], Training Accuracy: 34.3750%, Training Loss: 1.3777%
Epoch [3/300], Step [7/225], Training Accuracy: 35.4911%, Training Loss: 1.3712%
Epoch [3/300], Step [8/225], Training Accuracy: 35.5469%, Training Loss: 1.3654%
Epoch [3/300], Step [9/225], Training Accuracy: 34.5486%, Training Loss: 1.3704%
Epoch [3/300], Step [10/225], Training Accuracy: 34.2188%, Training Loss: 1.3628%
Epoch [3/300], Step [11/225], Training Accuracy: 33.2386%, Training Loss: 1.3677%
Epoch [3/300], Step [12/225], Training Accuracy: 33.3333%, Training Loss: 1.3652%
Epoch [3/300], Step [13/225], Training Accuracy: 33.1731%, Training Loss: 1.3664%
Epoch [3/300], Step [14/225], Training Accuracy: 32.5893%, Training Loss: 1.3697%
Epoch [3/300], Step [15

...

Epoch [298/300], Step [191/225], Training Accuracy: 99.7873%, Training Loss: 0.0134%
Epoch [298/300], Step [192/225], Training Accuracy: 99.7884%, Training Loss: 0.0134%
Epoch [298/300], Step [193/225], Training Accuracy: 99.7895%, Training Loss: 0.0134%
Epoch [298/300], Step [194/225], Training Accuracy: 99.7906%, Training Loss: 0.0134%
Epoch [298/300], Step [195/225], Training Accuracy: 99.7917%, Training Loss: 0.0134%
Epoch [298/300], Step [196/225], Training Accuracy: 99.7927%, Training Loss: 0.0134%
Epoch [298/300], Step [197/225], Training Accuracy: 99.7938%, Training Loss: 0.0134%
Epoch [298/300], Step [198/225], Training Accuracy: 99.7948%, Training Loss: 0.0134%
Epoch [298/300], Step [199/225], Training Accuracy: 99.7959%, Training Loss: 0.0134%
Epoch [298/300], Step [200/225], Training Accuracy: 99.7969%, Training Loss: 0.0133%
Epoch [298/300], Step [201/225], Training Accuracy: 99.7979%, Training Loss: 0.0133%
Epoch [298/300], Step [202/225], Training Accuracy: 99.7989%, Tra

Epoch [299/300], Step [67/225], Training Accuracy: 99.7901%, Training Loss: 0.0137%
Epoch [299/300], Step [68/225], Training Accuracy: 99.7932%, Training Loss: 0.0136%
Epoch [299/300], Step [69/225], Training Accuracy: 99.7962%, Training Loss: 0.0136%
Epoch [299/300], Step [70/225], Training Accuracy: 99.7991%, Training Loss: 0.0136%
Epoch [299/300], Step [71/225], Training Accuracy: 99.8019%, Training Loss: 0.0136%
Epoch [299/300], Step [72/225], Training Accuracy: 99.8047%, Training Loss: 0.0135%
Epoch [299/300], Step [73/225], Training Accuracy: 99.8074%, Training Loss: 0.0134%
Epoch [299/300], Step [74/225], Training Accuracy: 99.8100%, Training Loss: 0.0134%
Epoch [299/300], Step [75/225], Training Accuracy: 99.7917%, Training Loss: 0.0136%
Epoch [299/300], Step [76/225], Training Accuracy: 99.7944%, Training Loss: 0.0137%
Epoch [299/300], Step [77/225], Training Accuracy: 99.7971%, Training Loss: 0.0136%
Epoch [299/300], Step [78/225], Training Accuracy: 99.7997%, Training Loss: 

Epoch [299/300], Step [166/225], Training Accuracy: 99.8494%, Training Loss: 0.0131%
Epoch [299/300], Step [167/225], Training Accuracy: 99.8503%, Training Loss: 0.0132%
Epoch [299/300], Step [168/225], Training Accuracy: 99.8419%, Training Loss: 0.0133%
Epoch [299/300], Step [169/225], Training Accuracy: 99.8336%, Training Loss: 0.0134%
Epoch [299/300], Step [170/225], Training Accuracy: 99.8346%, Training Loss: 0.0135%
Epoch [299/300], Step [171/225], Training Accuracy: 99.8355%, Training Loss: 0.0135%
Epoch [299/300], Step [172/225], Training Accuracy: 99.8365%, Training Loss: 0.0134%
Epoch [299/300], Step [173/225], Training Accuracy: 99.8284%, Training Loss: 0.0135%
Epoch [299/300], Step [174/225], Training Accuracy: 99.8294%, Training Loss: 0.0135%
Epoch [299/300], Step [175/225], Training Accuracy: 99.8304%, Training Loss: 0.0135%
Epoch [299/300], Step [176/225], Training Accuracy: 99.8313%, Training Loss: 0.0135%
Epoch [299/300], Step [177/225], Training Accuracy: 99.8323%, Tra

Epoch [300/300], Step [38/225], Training Accuracy: 99.8766%, Training Loss: 0.0123%
Epoch [300/300], Step [39/225], Training Accuracy: 99.8397%, Training Loss: 0.0130%
Epoch [300/300], Step [40/225], Training Accuracy: 99.8438%, Training Loss: 0.0131%
Epoch [300/300], Step [41/225], Training Accuracy: 99.8476%, Training Loss: 0.0129%
Epoch [300/300], Step [42/225], Training Accuracy: 99.8512%, Training Loss: 0.0128%
Epoch [300/300], Step [43/225], Training Accuracy: 99.8547%, Training Loss: 0.0126%
Epoch [300/300], Step [44/225], Training Accuracy: 99.8580%, Training Loss: 0.0125%
Epoch [300/300], Step [45/225], Training Accuracy: 99.8611%, Training Loss: 0.0123%
Epoch [300/300], Step [46/225], Training Accuracy: 99.8641%, Training Loss: 0.0122%
Epoch [300/300], Step [47/225], Training Accuracy: 99.8670%, Training Loss: 0.0122%
Epoch [300/300], Step [48/225], Training Accuracy: 99.8047%, Training Loss: 0.0129%
Epoch [300/300], Step [49/225], Training Accuracy: 99.8087%, Training Loss: 

Epoch [300/300], Step [136/225], Training Accuracy: 99.8047%, Training Loss: 0.0127%
Epoch [300/300], Step [137/225], Training Accuracy: 99.8061%, Training Loss: 0.0127%
Epoch [300/300], Step [138/225], Training Accuracy: 99.8075%, Training Loss: 0.0126%
Epoch [300/300], Step [139/225], Training Accuracy: 99.7977%, Training Loss: 0.0126%
Epoch [300/300], Step [140/225], Training Accuracy: 99.7991%, Training Loss: 0.0127%
Epoch [300/300], Step [141/225], Training Accuracy: 99.7895%, Training Loss: 0.0128%
Epoch [300/300], Step [142/225], Training Accuracy: 99.7909%, Training Loss: 0.0128%
Epoch [300/300], Step [143/225], Training Accuracy: 99.7924%, Training Loss: 0.0127%
Epoch [300/300], Step [144/225], Training Accuracy: 99.7938%, Training Loss: 0.0127%
Epoch [300/300], Step [145/225], Training Accuracy: 99.7953%, Training Loss: 0.0127%
Epoch [300/300], Step [146/225], Training Accuracy: 99.7967%, Training Loss: 0.0126%
Epoch [300/300], Step [147/225], Training Accuracy: 99.7980%, Tra

In [23]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 32.40689271817676 %
